In [34]:
import tensorflow as tf
import pandas as pd
import numpy as np
import cv2
from PIL import Image
import mediapipe as mp
from sklearn.ensemble import RandomForestClassifier
import plotly.express as px
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split
from tqdm.notebook import tqdm

## Load Model

In [7]:
model = tf.keras.models.load_model('embedding_model_2023-06-03.h5')
model.summary()

Model: "Embedding"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_14 (InputLayer)       [(None, 478, 3)]          0         
                                                                 
 flatten_13 (Flatten)        (None, 1434)              0         
                                                                 
 batch_normalization_13 (Bat  (None, 1434)             5736      
 chNormalization)                                                
                                                                 
 dense_78 (Dense)            (None, 1024)              1469440   
                                                                 
 dropout_22 (Dropout)        (None, 1024)              0         
                                                                 
 dense_79 (Dense)            (None, 16)                16400     
                                                         

## Preprocessing Helper Functions

In [12]:
from model import LandmarkExtractor
lmk_extractor = LandmarkExtractor()

def preprocess(landmark_extractor: LandmarkExtractor, image: bytes) -> np.ndarray:
    array_repr = np.asarray(bytearray(image), dtype=np.uint8)
    # Decode the image. If there is no color, cv2.IMREAD_GRAYSCALE can be used
    try:
        decoded_img = cv2.imdecode(array_repr, flags=cv2.IMREAD_COLOR)
    except:
        decoded_img = cv2.imdecode(array_repr, flags=cv2.IMREAD_GRAYSCALE)
    landmarks = landmark_extractor.extract_landmarks_flat(decoded_img)
    if landmarks is None:
        return None
    return pd.DataFrame([landmarks]).to_numpy().reshape(1, 478, -1)

INFO: Created TensorFlow Lite XNNPACK delegate for CPU.


In [13]:
def extract_face(face_detection, image):
    mp_face_detection = mp.solutions.face_detection
    image = cv2.imdecode(image, cv2.IMREAD_COLOR)

    # Convert the image to RGB
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

    # Initialize the face detection model

    # Run the face detection model on the image
    results = face_detection.process(image)
    # If a face is detected, crop the image to the face box
    if results.detections:
        for detection in results.detections:
            x, y, w, h = (
                int(
                    detection.location_data.relative_bounding_box.xmin * image.shape[1]
                ),
                int(
                    detection.location_data.relative_bounding_box.ymin * image.shape[0]
                ),
                int(
                    detection.location_data.relative_bounding_box.width * image.shape[1]
                ),
                int(
                    detection.location_data.relative_bounding_box.height
                    * image.shape[0]
                ),
            )
            cropped_image = image[y : y + h, x : x + w]
            return cv2.cvtColor(cropped_image, cv2.COLOR_RGB2BGR)

In [14]:
def embed(model, image):
    landmarks = preprocess(lmk_extractor, image)
    if landmarks is None:
        return None
    return model.predict(landmarks)

## Load Datasets
### FER 2013

In [39]:
fer_df = pd.read_csv("data/fer2013/labels.clean.csv", index_col=0)

In [40]:
def extract_label(row: pd.Series):
    return row.drop(["Usage"]).sort_values(ascending=False).index[0]

In [45]:
import os


def load_fer_dataset(df: pd.DataFrame, mode: str = "Training"):
    embeddings = []
    labels = []
    df = df[df["Usage"] == mode]
    for image_name, row in tqdm(df.iterrows(), total=len(df)):
        with open(os.path.join("data", "fer2013", "FER2013Test" if mode == "Test" else "FER2013Train", image_name), "rb") as f:
            image = f.read()
        embeddings.append(
            embed(model, image)
        )
        labels.append(
            extract_label(row)
        )
    X = np.array(embeddings)
    y = np.array(labels)
    return X, y

In [59]:
X_train, y_train = load_fer_dataset(fer_df, mode="Training")
# X_test, y_test = load_fer_dataset(fer_df, mode="Testing")

0it [00:00, ?it/s]

In [60]:
X_train, X_test, y_train, y_test = train_test_split(X_train, y_train, test_size=0.2)

## Train Classifier

In [120]:
# from sklearn.model_selection import GridSearchCV
# param_grid = {
#     'bootstrap': [True],
#     'max_depth': [80, 90, 100, 110],
#     'max_features': [2, 3, 4, 5],
#     'min_samples_leaf': [3, 4, 5],
#     'min_samples_split': [8, 10, 12],
#     'n_estimators': [100, 200, 300, 1000]
# }
# rf = RandomForestClassifier()
# clf = GridSearchCV(estimator = rf, param_grid = param_grid, cv = 3, verbose = 2, n_jobs = -1)
# clf.fit(X_train.squeeze(), y_train)

In [121]:
clf = RandomForestClassifier()
clf.fit(X_train.squeeze(), y_train)

RandomForestClassifier()

## Evaluate Classifier

In [122]:
print(classification_report(y_test, clf.predict(X_test.squeeze())))

              precision    recall  f1-score   support

       anger       0.62      0.24      0.34       432
    contempt       0.75      0.10      0.17        31
     disgust       1.00      0.19      0.32        31
        fear       0.88      0.13      0.23       116
   happiness       0.71      0.75      0.73      1460
     neutral       0.59      0.86      0.70      1939
     sadness       0.51      0.17      0.26       623
    surprise       0.69      0.57      0.62       680
     unknown       1.00      0.14      0.24        22

    accuracy                           0.63      5334
   macro avg       0.75      0.35      0.40      5334
weighted avg       0.64      0.63      0.60      5334



In [123]:
cm = confusion_matrix(y_test, clf.predict(X_test.squeeze()), labels=clf.classes_, normalize="pred")
fig = px.imshow(cm, x=clf.classes_, y=clf.classes_, title="Confusion Matrix - Precision")
fig.update_xaxes(side="top", title="Predicted")
fig.update_yaxes(title="Actual")
fig.show()
fig.write_image("confusion_matrix_precision.svg")

In [124]:
cm = confusion_matrix(y_test, clf.predict(X_test.squeeze()), labels=clf.classes_, normalize="true")
fig = px.imshow(cm, x=clf.classes_, y=clf.classes_, title="Confusion Matrix - Recall")
fig.update_xaxes(side="top", title="Predicted")
fig.update_yaxes(title="Actual")
fig.show()
fig.write_image("confusion_matrix_recall.svg")

In [125]:
# plot roc curve using plotly express
from cv2 import line
from sklearn.metrics import roc_curve, auc

y_score = clf.predict_proba(X_test.squeeze())
fpr = dict()
tpr = dict()
roc_auc = dict()
for i, class_name in enumerate(clf.classes_):
    fpr[i], tpr[i], _ = roc_curve(y_test == clf.classes_[i], y_score[:, i])
    roc_auc[class_name] = auc(fpr[i], tpr[i])

# plot roc curve
fig = px.line(
    x=[0, 1],
    y=[0, 1],
    title="ROC Curve",
    labels=dict(x="False Positive Rate", y="True Positive Rate"),
    color_discrete_sequence=["lightgrey"],
    line_dash_sequence=["dot"],
)
for i in range(len(clf.classes_)):
    fig.add_scatter(
        x=fpr[i],
        y=tpr[i],
        name=f"{clf.classes_[i]}",
    )
fig.show()
fig.write_image("roc_curve.svg")

In [126]:
roc_auc

{'anger': 0.7750016055427112,
 'contempt': 0.6764034964992427,
 'disgust': 0.6472994592227163,
 'fear': 0.7823449333209975,
 'happiness': 0.9045211844329247,
 'neutral': 0.8308803636084676,
 'sadness': 0.7416447554696789,
 'surprise': 0.8969975226876312,
 'unknown': 0.6664199411281488}